In [7]:
import sys
sys.path.append("..//src")
import os
import datetime
import pandas as pd
import numpy as np
from example_lorenz import get_lorenz_data
from sindy_utils import library_size
import training
import torch
print(torch.cuda.is_available())


True


# Generate data

In [8]:

# generate training, validation, testing data
noise_strength = 1e-6
training_data = get_lorenz_data(1024, noise_strength=noise_strength)
validation_data = get_lorenz_data(20, noise_strength=noise_strength)
training_data['x'] = torch.tensor(training_data['x']).float().to('cuda')
training_data['dx'] = torch.tensor(training_data['dx']).float().to('cuda')
training_data['t'] = torch.tensor(training_data['t']).float().to('cuda')
training_data['z'] = torch.tensor(training_data['z']).float().to('cuda')
training_data['dz'] = torch.tensor(training_data['dz']).float().to('cuda')
training_data['ddx'] = None

validation_data['x'] = torch.tensor(validation_data['x']).float().to('cuda')
validation_data['dx'] = torch.tensor(validation_data['dx']).float().to('cuda')
validation_data['t'] = torch.tensor(validation_data['t']).float().to('cuda')
validation_data['z'] = torch.tensor(validation_data['z']).float().to('cuda')
validation_data['dz'] = torch.tensor(validation_data['dz']).float().to('cuda')
validation_data['ddx'] = None


# Set up model and training parameters

In [9]:
params = {}

params['input_dim'] = 128
params['latent_dim'] = 3
params['model_order'] = 1
params['poly_order'] = 3
params['include_sine'] = False
params['library_dim'] = library_size(params['latent_dim'], params['poly_order'], params['include_sine'], True)

# sequential thresholding parameters
params['sequential_thresholding'] = True
params['coefficient_threshold'] = 0.1
params['threshold_frequency'] = 500
params['coefficient_mask'] = torch.ones((params['library_dim'], params['latent_dim']))
params['coefficient_initialization'] = 'constant'

# loss function weighting
params['loss_weight_decoder'] = 1.0
params['loss_weight_sindy_z'] = 0
params['loss_weight_sindy_x'] = 1e-4
params['loss_weight_sindy_regularization'] = 1e-5

params['activation'] = 'sigmoid'
params['widths'] = [64, 32]
print(params['widths'][::-1])
# training parameters
params['epoch_size'] = training_data['x'].shape[0]
params['batch_size'] = 1024
params['learning_rate'] = 2e-4

params['data_path'] = os.getcwd() + '/'
params['print_progress'] = True
params['print_frequency'] = 1

# training time cutoffs
params['max_epochs'] = 5001
params['refinement_epochs'] = 1001

[32, 64]


In [10]:
import numpy as np
import torch

def to_numpy(obj):
    if isinstance(obj, torch.Tensor):
        return obj.cpu().numpy()  # Convert tensor to numpy array
    elif isinstance(obj, dict):
        return {k: to_numpy(v) for k, v in obj.items()}  # Apply recursively to dictionaries
    elif isinstance(obj, list):
        return [to_numpy(v) for v in obj]  # Apply recursively to lists
    else:
        return obj  # Return the object as is if it's neither a tensor, list, nor dictionary


# Run training experiments

In [11]:
num_experiments = 1
df = pd.DataFrame()
for i in range(num_experiments):
    print('EXPERIMENT %d' % i)

    if i == 2:
        params['learning_rate'] = 1e-4

    params['coefficient_mask'] = torch.ones((params['library_dim'], params['latent_dim']))

    params['save_name'] = 'lorenz_' + datetime.datetime.now().strftime("%Y_%m_%d_%H_%M_%S_%f")
    
    results_dict = training.train_network(training_data, validation_data, params)
    results_dict = to_numpy(results_dict)
    params = to_numpy(params)

    df = df._append({**results_dict, **params}, ignore_index=True)

df.to_pickle('experiment_results_' + datetime.datetime.now().strftime("%Y%m%d%H%M") + '.pkl')

EXPERIMENT 0
Device: cuda:0
TRAINING


c:\Users\ianma\Desktop\Study\Python\CS4240_DeepLearning_Group41_ReproducibilityProject\Autoencoders-Reproduction\examples\..//src\training.py:181: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  'x': torch.tensor(data['x'][idxs], dtype=torch.float32).to(params['device']),
c:\Users\ianma\Desktop\Study\Python\CS4240_DeepLearning_Group41_ReproducibilityProject\Autoencoders-Reproduction\examples\..//src\training.py:182: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  'dx': torch.tensor(data['dx'][idxs], dtype=torch.float32).to(params['device']),
c:\Users\ianma\Desktop\Study\Python\CS4240_DeepLearning_Group41_ReproducibilityProject\Autoencoders-Reproduction\examples\..//src\training.py:188: UserW

Epoch 0
   Training Total Loss: 0.09573201090097427
   Training decoder Loss: 0.09441116452217102
   Training sindy_z Loss: 9.11255931854248
   Training sindy_x Loss: 13.11302661895752
   Training sindy_regularization Loss: 0.9542178511619568
   Validation Total Loss: 0.09332571178674698
   Validation decoder Loss: 0.09221326559782028
   Validation sindy_z Loss: 7.986013412475586
   Validation sindy_x Loss: 11.02900218963623
   Validation sindy_regularization Loss: 0.9542178511619568
Decoder Loss Ratio: 0.500340, Decoder SINDy Loss Ratio: 1.000030
Epoch 1
   Training Total Loss: 0.08436557650566101
   Training decoder Loss: 0.08304361253976822
   Training sindy_z Loss: 203.0198974609375
   Training sindy_x Loss: 13.128555297851562
   Training sindy_regularization Loss: 0.9110050797462463
   Validation Total Loss: 0.08255094289779663
   Validation decoder Loss: 0.08143698424100876
   Validation sindy_z Loss: 187.4336395263672
   Validation sindy_x Loss: 11.048479080200195
   Validation 

c:\Users\ianma\Desktop\Study\Python\CS4240_DeepLearning_Group41_ReproducibilityProject\Autoencoders-Reproduction\examples\..//src\training.py:59: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  loss_val, _, _ = autoencoder_network.define_loss(torch.tensor(train_dict['x'], dtype=torch.float32), torch.tensor(train_dict['dx'], dtype=torch.float32), train_dict['ddx'], params=params)


Epoch 0
   Training Total Loss: 1.2786677871190477e-05
   Training decoder Loss: 5.482540359480481e-07
   Training sindy_z Loss: 3.0357959270477295
   Training sindy_x Loss: 0.005960995797067881
   Training sindy_regularization Loss: 1.1642324924468994
   Validation Total Loss: 1.4300897419161629e-05
   Validation decoder Loss: 8.185797355508839e-07
   Validation sindy_z Loss: 3.0511255264282227
   Validation sindy_x Loss: 0.018399935215711594
   Validation sindy_regularization Loss: 1.1642324924468994
Decoder Loss Ratio: 0.000004, Decoder SINDy Loss Ratio: 0.001668
Epoch 1
Epoch 1
   Training Total Loss: 1.3027496606810018e-05
   Training decoder Loss: 7.646048061360489e-07
   Training sindy_z Loss: 3.027841567993164
   Training sindy_x Loss: 0.006223864853382111
   Training sindy_regularization Loss: 1.164050579071045
   Validation Total Loss: 1.4891151295159943e-05
   Validation decoder Loss: 1.3793021480523748e-06
   Validation sindy_z Loss: 3.043004274368286
   Validation sindy_x 

c:\Users\ianma\Desktop\Study\Python\CS4240_DeepLearning_Group41_ReproducibilityProject\Autoencoders-Reproduction\examples\..//src\training.py:73: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  loss_val, final_losses, _ = autoencoder_network.define_loss(torch.tensor(validation_dict['x'], dtype=torch.float32), torch.tensor(validation_dict['dx'], dtype=torch.float32),validation_dict['ddx'], params=params)
c:\Users\ianma\Desktop\Study\Python\CS4240_DeepLearning_Group41_ReproducibilityProject\Autoencoders-Reproduction\examples\..//src\training.py:75: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  _, _, _, _, _, _, _, sindy_predict = autoencoder_network(torch.tensor(validation_dict['x'], dtype=t

In [12]:
print(results_dict)
    
print(params)

{'num_epochs': 5000, 'x_norm': array(0.18430132, dtype=float32), 'sindy_predict_norm_x': array(11.028677, dtype=float32), 'sindy_predict_norm_z': 26.36937141418457, 'sindy_coefficients': array([[-1.6068832e-04, -8.4667749e+00,  1.6882240e+00],
       [ 2.1262820e-05, -2.2550987e-04, -1.2568021e-04],
       [ 4.3010845e+00,  4.8594775e+00, -3.2642603e-04],
       [-7.7740588e+00,  2.1084229e-04, -5.4710960e+00],
       [-3.4834149e-01,  1.2570344e+00, -1.2203063e+00],
       [ 3.7389355e+00,  1.5845215e-04, -2.4293490e-04],
       [-1.4103157e-04,  2.3422355e-04,  3.7376752e+00],
       [-3.7981043e-04, -1.6044545e+00, -8.3866996e-01],
       [-1.1861203e-04, -1.0206042e-02,  1.1296527e+00],
       [ 1.2979560e+00, -1.7308425e-04,  2.2007334e+00],
       [-1.6703261e-01,  3.7592518e-01, -8.3222359e-02],
       [ 2.0023696e-04, -5.8406532e-01, -8.5545421e-01],
       [-2.4886624e-04,  2.5640771e-04,  1.1255543e-01],
       [-4.2578360e-04,  2.1697046e-01,  6.7650862e-02],
       [ 8.4284